In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px


# определим кодировки
#from chardet.universaldetector import UniversalDetector # Импортируем субмодуль chardet.universaldetector
#detector = UniversalDetector()
#with open('data/Справочник Номенклатуры.xlsx', 'rb') as fh:
#    for line in fh:
#        detector.feed(line)
#        if detector.done:
#            break
#detector.close()

nomen_data = pd.read_excel('data/Справочник Номенклатуры.xlsx')
sales_data = pd.read_excel('data/Продажи_дляП1.xlsx')
price_data = pd.read_excel('data/ПрайсДляП.xlsx')
stock_data = pd.read_excel('data/Остатки_дляП1.xlsx')

In [ ]:
display(nomen_data.shape)
m = nomen_data.shape[1] 
nomen_data = nomen_data.dropna( how='any' ,thresh=m-2 ,axis=0)



In [ ]:

#Обработаем остатки
stock_data['Дата'] = pd.to_datetime(stock_data['ДАТА'], dayfirst=True) 
stock_data['Артикул'] = stock_data['АРТИКУЛ']
stock_data = stock_data.drop(['ДАТА','Маркер', 'АРТИКУЛ'],axis=1)

In [ ]:
sales_data['Дата'] = pd.to_datetime(sales_data['Дата'], dayfirst=True)
sales_data['Дата'] = sales_data['Дата'].dt.date
sales_data['Дата'] = pd.to_datetime(sales_data['Дата'], dayfirst=True)
sales_data['Артикул'] = sales_data['Артикул']

In [ ]:
display(nomen_data.head())
display(sales_data.head())
display(price_data.head())
display(stock_data.head())

In [ ]:
# сцепим вместе все данные в одну таблицу
myst_data = pd.merge(left = stock_data, right= sales_data, on = ['Дата','Артикул'], how = 'outer')
myst_data = pd.merge(left = myst_data, right= price_data, on = 'Артикул', how = 'left')
myst_data = pd.merge(left = myst_data, right= nomen_data, on = 'Артикул', how = 'left')
myst_data = myst_data.fillna({'Продажи бе':0, 'Остаток бе':0}) # уберем отсутствующие продажи и остатки
myst_data['Продажи руб'] = myst_data['Продажи бе'] * myst_data['Цена']
myst_data['Остаток руб'] = myst_data['Остаток бе'] * myst_data['Цена']
myst_data.info()

In [ ]:
# добавим дополнительные показатели
# Добавим данные о клиентах к артикулу (доля лучшего/лучший клиент/сколько всего клиентов)
# создадим базовые данные для сборки информации по артикулам
art_data = myst_data.groupby(
                                by=['Артикул'],
                                as_index=False
                                )['Продажи руб'].sum()

#создадим дата сет артикул-клиент
client_data = myst_data.groupby(
                                by=['Артикул', 'КЛИЕНТ'],
                                as_index=False
                                )['Продажи руб'].sum().sort_values(by='Продажи руб', ascending=False)

# функция определения имени клиента с макс продажами
def get_max_client_name(art):
    if len(client_data[client_data['Артикул'] == art]['КЛИЕНТ'].values)<1:
        return np.nan
    else: 
        return client_data[client_data['Артикул'] == art]['КЛИЕНТ'].iloc[0]

#создадим поля Продажи макс клиента, Макс клиент и Доля макс клиента
art_data['Продажи макс клиента руб'] = art_data['Артикул'].apply(lambda x: client_data[client_data['Артикул'] == x]['Продажи руб'].max())
art_data['Макс Клиент'] = art_data['Артикул'].apply(get_max_client_name)
art_data['Доля Макс Клиента'] = art_data['Продажи макс клиента руб'] / art_data['Продажи руб']

#создадим поле Число клиентоа
client_data = client_data['Артикул'].value_counts()
def get_client_count(art):
    try:
        res = client_data.loc[art]
    except:
        return np.nan
    return client_data.loc[art]

art_data['Число клиентов'] = art_data['Артикул'].apply(get_client_count) 

display(art_data.head())

In [ ]:
# Создадим поле связанное с частотой продаж
freq_data = myst_data.groupby(
                                by=['Артикул','Дата'],
                                as_index=False
                                )['Продажи руб'].sum()
display(freq_data.head())
date_num = myst_data['Дата'].unique().shape[0]

def get_freq_count(art):
    return freq_data[(freq_data['Артикул'] == art) & (freq_data['Продажи руб'] > 0)].shape[0]/date_num

art_data['Частота'] = art_data['Артикул'].apply(get_freq_count) 

# cколько всего активных дат в таблице


In [ ]:
#Создадим статистические метрики по датам
freq_data_mod = freq_data.groupby(
                                by=['Артикул'],
                                as_index=False
                                )['Продажи руб'].agg(['mean','std','median'])

display(freq_data_mod.head())
art_data['Среднеедневная'] = art_data['Артикул'].apply(lambda x: freq_data_mod['mean'].loc[x]) 
art_data['Медиана'] = art_data['Артикул'].apply(lambda x: freq_data_mod['median'].loc[x]) 
art_data['std'] = art_data['Артикул'].apply(lambda x: freq_data_mod['std'].loc[x]) 
art_data['std'] = art_data['std'] / art_data['Среднеедневная']
art_data['std'] = art_data['std'].apply(lambda x: x if x<3 else 3)
display(art_data.head())

In [ ]:
#создадим поле связанное с наличием
stock_data = myst_data.groupby(
                                by=['Артикул','Дата'],
                                as_index=False
                                )['Остаток руб'].mean()
display(stock_data.head())

def get_stock_count(art):
    return stock_data[(stock_data['Артикул'] == art) & (stock_data['Остаток руб'] > 0) ].shape[0]/date_num

art_data['Наличие'] = art_data['Артикул'].apply(get_stock_count)
display(art_data.shape)

art_data = pd.merge(left = art_data, right= nomen_data, on = 'Артикул', how = 'left')
display(art_data.shape)

In [ ]:
# Создадим наши категориальные признаки медианы
art_data['Категория медианы'] = art_data['Медиана']/art_data['Среднеедневная']

def set_median_cat(cat):
    if cat == np.nan:
        return np.nan
    elif cat >= 1.0:
        return 'Разовый по медиане'
    elif cat == 0:
        return 'Редкий по медиане'
    else:
        return 'Стандарт по медиане'

art_data['Категория медианы'] = art_data['Категория медианы'].apply(set_median_cat)

# Создадим наши категориальный признак Продажи/Средние продажи
art_data['Наклон нормальности'] =  art_data['Продажи руб']/art_data['Среднеедневная']
k_norm = art_data[art_data["Доля Макс Клиента"]<0.75]['Наклон нормальности'].mean()
# если Продажи руб - (Среднее - 2000)* коэф >= 0
art_data['Категория нормальности'] = art_data['Продажи руб'] -  (art_data['Среднеедневная']) * k_norm
art_data['Категория нормальности'] = art_data['Категория нормальности'].apply(lambda x: 'Нормальная' if x>=0 else 'Ненормальная')

art_data['Категория Стат'] = art_data['Категория нормальности'] + ' ' + art_data['Категория медианы']

In [37]:
import plotly.graph_objs as go 
df = art_data[(art_data['Доля Макс Клиента'] <=1 ) & (art_data['Доля Макс Клиента'] > 0 )]
#df['Продажи руб'] = df['Продажи руб'].apply(lambda x: x if x< 500000 else 500000)
df['Продажи руб'] = df['Продажи руб'].apply(lambda x: 1 if x< 1 else x)

#fig = px.histogram(df, x= 'Продажи руб', 
#                 title='Распределение продаж', width=1200, height=500,
#                 marginal="box",text_auto=True)
#fig.show()

#fig = px.histogram(df, x= 'Число клиентов', 
#                 title='Распределение числа клиентов', width=1200, height=500,
#                 marginal="box",text_auto=True)
#fig.show()
#
#fig = px.histogram(df, x= 'Частота', 
#                 title='Распределение частоты заказов', width=1200, height=500,
#                 marginal="box",text_auto=True)
#fig.show()
#
#fig = px.histogram(df, x= 'Наличие', 
#                 title='Распределение наличия', width=1200, height=500,
#                 marginal="box",text_auto=True)
#fig.show()
#
#fig = px.histogram(df, x= 'Доля Макс Клиента', 
#                 title='Распределение доли макс клиента', width=1200, height=500,
#                 marginal="box",text_auto=True)
#fig.show()
#
fig = px.scatter_matrix(df,
    dimensions=["Продажи руб", "Доля Макс Клиента", "Число клиентов", "Частота", 'Наличие','Медиана','std','Среднеедневная'], width=1200, height=1200, title='Вычисление зависимостей в номенклатуре')
fig.show()


#fig = px.scatter(df, x= 'Число клиентов', y= 'Частота', color='Продажи руб', color_continuous_scale='oryel',
#                 title='Зависимость числа клиентов и частоты покупок', width=1000, height=700)
#                 #marginal_x="histogram", marginal_y="histogram")
#fig.show()

fig = px.scatter(df, x= 'Среднеедневная', y= 'Продажи руб', log_x=True, log_y=True,
                 title='Зависимость среднедневных продаж и суммы продаж', width=1000, height=700,
                  color = 'Категория Стат')


x = np.arange(0, 60000, 1)
fig.add_trace(go.Scatter(x=x, y=k_norm*(x)  , name='Линия Продажа = коэф * ср день')) # Рисуем y = x

fig.show()

df2 = df
df2['Медиана1'] = df['Медиана'].apply(lambda x: x+1)

fig = px.scatter(df2, x= 'Среднеедневная', y= 'Медиана1', log_x=True, log_y=True, 
                 title='Зависимость средних и медианных продаж', width=1000, height=700,
                  color = 'Категория Стат')
fig.show()

fig = px.scatter_3d(
    data_frame=df2, #DataFrame
    x = 'Продажи руб', #ось абсцисс
    y = 'Медиана1', #ось ординат
    z = 'Среднеедневная', #ось аппликат
    color="std", #расцветка в зависимости от страны
    log_x=True, 
    log_y=True,
    log_z=True,
    width=1000,
    height=700
)

fig.show()

#display(df[df["Число клиентов"] > 100])
#display(k_norm)

df1 = df[df['Категория Стат'] == 'Нормальная Стандарт по медиане']
fig = px.scatter(df1, y= "Продажи руб", x= "Число клиентов", 
                 title='Зависимость средних и медианных продаж', width=1000, height=700,
                  color = 'Доля Макс Клиента')
fig.show()




df_cat = df.groupby(
                                by='Категория Стат',
                                as_index=False
                                )['Продажи руб'].sum()

fig = px.bar(df_cat, y="Продажи руб", x='Категория Стат', text_auto=True)
fig.show()

df_cat = df.groupby(
                                by='Категория Стат',
                                as_index=False
                                )['Категория Стат'].value_counts()

fig = px.bar(df_cat, y="count", x='Категория Стат',text_auto=True)
fig.show()

display(df[df['Категория Стат'] == 'Нормальная Редкий по медиане'].sort_values(by='Продажи руб', ascending=False))

display(df[(df['Артикул'] == 297560) | (df['Артикул'] == 296565)])
#df[df['Категория Стат'] == 'Нормальная Редкий по медиане'].sort_values(by='Продажи руб', ascending=False).to_excel('data/analysis1.xlsx')

C:\Users\Кирилл Шемонаев\AppData\Local\Temp\ipykernel_19784\3664307463.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



C:\Users\Кирилл Шемонаев\AppData\Local\Temp\ipykernel_19784\3664307463.py:52: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Артикул  Продажи руб  Продажи макс клиента руб  \
3100  294010а  1845349.545               1840589.400   
1258   296565  1761305.000               1761305.000   
1210   294155  1459016.208               1444987.206   
2863  255054ч  1303238.160               1281102.480   
1217   295010  1143266.670               1133561.520   
...       ...          ...                       ...   
1444   337236       20.200                    20.200   
3161  300452/       18.380                    18.380   
3220  317100г       16.960                    16.960   
1551   413147       11.910                    11.910   
3940  477016е        1.000                  -709.120   

                       Макс Клиент  Доля Макс Клиента  Число клиентов  \
3100         КРОШКА-КАРТОШКА-М ООО           0.997420             3.0   
1258              МУЛЬТИПРО ООО ТК           1.000000             1.0   
1210         КРОШКА-КАРТОШКА-М ООО           0.990385             3.0   
2863                  ХАТИМАКИ ООО           0.983015             4.0   
1217         КРОШКА-КАРТОШКА-М ООО           0.991511             5.0   
...                            ...                ...             ...   
1444  Матвеева Оксана Владимировна           1.000000             1.0   
3161              Артовский Малька           1.000000             1.0   
3220             НЬЮ ДЭЙ МЕДИА ООО           1.000000             1.0   
1551                Гребцова Ольга           1.000000             1.0   
3940                       КИС ООО           1.000000             1.0   

       Частота  Среднеедневная  Медиана       std  ...  \
3100  0.318182    25629.854792      0.0  1.403596  ...   
1258  0.056818    27957.222222      0.0  3.000000  ...   
1210  0.227273    20549.524056      0.0  1.776101  ...   
2863  0.352273    18100.530000      0.0  1.968363  ...   
1217  0.340909    15878.703750      0.0  1.391697  ...   
...        ...             ...      ...       ...  ...   
1444  0.011364        0.280556      0.0  3.000000  ...   
3161  0.011364        0.255278      0.0  3.000000  ...   
3220  0.011364        0.249412      0.0  3.000000  ...   
1551  0.011364        0.167746      0.0  3.000000  ...   
3940  0.000000     -236.373333      0.0 -1.732051  ...   

                                         Проект  Категория  \
3100                                2. Упаковка  под заказ   
1258                                2. Упаковка  под заказ   
1210                                2. Упаковка  под заказ   
2863                                2. Упаковка        NaN   
1217                                2. Упаковка        NaN   
...                                         ...        ...   
1444  3. Сервировка стола и товары для клининга        NaN   
3161  3. Сервировка стола и товары для клининга        NaN   
3220  3. Сервировка стола и товары для клининга        NaN   
1551  3. Сервировка стола и товары для клининга        NaN   
3940  3. Сервировка стола и товары для клининга  под заказ   

                    Основной поставщик  Артикул производителя       Статус  \
3100                        ПЕРИНТ АО              0,55/111/К  Действующая   
1258                        ПЕРИНТ АО              1400/223/К  Действующая   
1210                ТД АЛЬЯНС УПАК ООО         ДВ-1,1/131 ОСВ  Действующая   
2863                   ДЖИДИСИ ЕАС ООО    ECO OpSalad 1000 BE  Действующая   
1217                        ПЕРИНТ АО              Крышка 111  Действующая   
...                                ...                    ...          ...   
1444                 СВЕЧНОЙМАРКЕТ ООО                   1428  Действующая   
3161  РУССКАЯ БУМАГА АЛЛ ПРОДУКЦИЯ ООО                      -  Действующая   
3220                       ГУСЛИЦА ООО                    NaN  Действующая   
1551                            САСПАК                    NaN  Действующая   
3940                    СИНЕРГЕТИК ООО                 109754  Действующая   

      Категория медианы Наклон нормальности Категория нормальности  \
3100  Р

Артикул  Продажи руб  Продажи макс клиента руб       Макс Клиент  \
1258  296565   1761305.00                 1761305.0  МУЛЬТИПРО ООО ТК   
1270  297560   1024494.12                 1004406.0  МУЛЬТИПРО ООО ТК   

      Доля Макс Клиента  Число клиентов   Частота  Среднеедневная  Медиана  \
1258           1.000000             1.0  0.056818    27957.222222      0.0   
1270           0.980392             2.0  0.068182    15290.957015      0.0   

      std  ...       Проект  Категория  Основной поставщик  \
1258  3.0  ...  2. Упаковка  под заказ          ПЕРИНТ АО    
1270  3.0  ...  2. Упаковка  под заказ          ПЕРИНТ АО    

      Артикул производителя       Статус  Категория медианы  \
1258             1400/223/К  Действующая  Редкий по медиане   
1270             крышка 223  Действующая  Редкий по медиане   

     Наклон нормальности Категория нормальности                Категория Стат  \
1258                63.0             Нормальная  Нормальная Редкий по медиане   
1270                67.0             Нормальная  Нормальная Редкий по медиане   

     Медиана1  
1258      1.0  
1270      1.0  

[2 rows x 27 columns]

### Категоризация 1.

Товары в доль линии концентрации Продажи руб / Среденедневные. Обозначим как "Пропорция продаваемости" - Правильная/Неправильная

### Категоризация 2.

Соотношение медианы и среднедневных продаж
* Медиана = 0. (Нерегулярные по медиане)
* Медиана = Среднее (Разовые по медиане)
* Медиана != Среднее (Стандартные по медиане)

In [32]:
df = myst_data[myst_data['Артикул'] == '192302в']
df_sales = df.groupby(
                                by=['Дата'],
                                as_index=False
                                )['Продажи руб'].sum()
df_stock = df.groupby(
                                by=['Дата'],
                                as_index=False
                                )['Остаток руб'].mean()

df_clients = df.groupby(
                                by=['Артикул','КЛИЕНТ'],
                                as_index=False
                                )['Продажи руб'].sum().sort_values('Продажи руб', ascending=False)
display(df_clients.head(10))

df = pd.merge(left = df_stock, right= df_sales, on = 'Дата', how = 'outer')






df['медиана'] = df['Продажи руб'].median()
df['среднее'] = df['Продажи руб'].mean()
df['std'] = df['Продажи руб'].std()
df['страховой запас на день'] = df['Продажи руб'].mean() * ( 1+ df['std']/df['Продажи руб'].mean())
df['страховой запас'] = df['страховой запас на день']*5
display(df.head())
fig = px.line(df, x="Дата", y=['Продажи руб','Остаток руб', 'медиана','среднее','страховой запас на день','страховой запас'] ) 
fig.show()

fig = px.box(df, x='Продажи руб')
fig.show()

Артикул           КЛИЕНТ  Продажи руб
0  192302в  ВАЙЛДБЕРРИЗ ООО       281.75

Дата  Остаток руб  Продажи руб  медиана   среднее        std  \
0 2022-06-19          0.0        24.50     24.5  35.21875  29.601652   
1 2022-06-26          0.0        98.00     24.5  35.21875  29.601652   
2 2022-07-03          0.0        12.25     24.5  35.21875  29.601652   
3 2022-07-10          0.0        12.25     24.5  35.21875  29.601652   
4 2022-07-24          0.0        61.25     24.5  35.21875  29.601652   

   страховой запас на день  страховой запас  
0                64.820402       324.102011  
1                64.820402       324.102011  
2                64.820402       324.102011  
3                64.820402       324.102011  
4                64.820402       324.102011

KeyboardInterrupt: 